### Variables
We have our system state defined as  - 
* SS: (n, nd, (ch1, st1, r1,m, tbm, sbm), (ch2, st2, r2,m, tb2,m, sb2,m),.. (chn, stn, rn,m, tbn,m, sbn,m))
    * n - total number of available buses
    * m - subscript that denotes route m
    * nd - number of buses deployed
    * chn -  charging state of bus n
    * stn - state of bus n (3 states: deployed, not-deployed, charging/refueling)
    * rn,m - the route on which the bus is deployed
    * tbn,m - the previous stop the bus travelled to (travel time)
    * sbn,m - the previous stop which was served by the bus (service time)
        * If tbn= sbn, generate travel time for tbn+1; tbn = tbn+1 if accepted
        * Else if tbn> sbn, generate service time for sbn+1; sbn = sbn+1 if accepted

* t - the clock time/current time
* nrm - number of buses required on route m
* btn - time array for monitoring travel time and service time related to each bus


### Pseudo-code
1. Start at t = 0
2. Generate requirements from route, nd (required number of buses):
    1. Check availability of buses & minimum fuel level/battery capacity required for the routes
    2. Choose number of buses, K, to be deployed based on checks
        1. If K<nd, deploy buses with higher fuel/battery level and recharge/refuel the rest
        2. Else, send buses for recharge/refuel
    3. For each bus k, in {1, 2,.. n}, after selecting a specific route m {stops - 1, 2,... M}:
    4. Initialize j = 0 (Depot_Start)
    5. Generate interarrival times for stop j, update time tbk,j
    6. Generate service time at stop j, update time sbk,j
    7. STOP if j = M; Else update j = j + 1, goto 2.b. 
3. Based on the time we update the System State (SS) and the concerned variables.

### Cases
1. We generate demand for the route at time t,
    Sub-task: Generating series of buses to be deployed
    1. Condition 1: number of buses required <= number of charged/fuelled buses
        1. Deploy buses based on descending order of fuel level/charge
        2. Send buses for refuelling/recharging, if they are below a certain threshold
    2. Condition 2: number of buses required > number of charged/fuelled buses
        1. Send buses for refuelling/recharging
        2. As soon as the bus finishes recharging/refueling, buses get sent to the route
2. Routing of buses:
    1. Route 0: based on type of the bus and refuelling need. Will be a refuelling/ recharging route for the bus
    2. Route 1 to m: Buses will go through the stops till they reach Depot_Stop


## Variables
#### Buses
* bus: ($ch_n, st_n, r_{n,m}, tb_{n,m}, sb_{n,m}$)
    * $ch_n$ - charging state of bus n
    * $st_n$ - state of bus n (3 states: deployed, not-deployed, charging/refueling)
    * $r_{n,m}$ - the route on which the bus is deployed
    * $tb_{n,m}$ - the previous stop the bus travelled to (travel time)
    * $sb_{n,m}$ - the previous stop which was served by the bus (service time)
        * If $tb_n$= $sb_n$, generate travel time for $tb_{n+1}$; $tb_n$ = $tb_{n+1}$ if accepted
        * Else if $tb_n$> $sb_n$, generate service time for $sb_{n+1}$; $sb_n$ = $sb_{n+1}$ if accepted
    * Arrival time - route generated arrays
    * Service Time - route generated arrays
    * 

___
### System State New
SS = (n_buses, curr_dem, buses_deployed, buses_recharge, buses_standstill)
SS = (n_buses, curr_dem, buses_deployed, buses_recharge, buses_standstill, route_1_buses, route_2_buses,....)

#### Monitoring System State 

| Time | System State | Bus | Charge | Route | State | Event | Process Time | Demand-Current | Demand-Actual | Demand-Charge |
| ---- | ------------ | --- | ------ | ----- | ----- | ----- | ------------ | -------------- | ------------- | ------------- |
| 0    | (1,1,1,0,0)  | 1   | 50     | '1'   | 1     | 0     | 0            | 0              | 0             | 15            |
| 10.3 | (1,0,1,0,0)  | 1   | 48     | '1'   | 1     | 1     | 10.3         | -              | -             | -             |
| 12.3 | (1,0,1,0,0)  | 1   | 47.5   | '1'   | 1     | 0     | 2.0          | -              | -             | -             |

___

#### Monitoring Bus Deployments

| Time | Demand-Current | Demand-Actual | Demand-Charge | Bus | Charge | Route | Event Array  | Time Array   |
| ---- | -------------- | ------------- | ------------- | --- | ------ | ----- | ------------ | ------------ |
| 0    | 0              | 0             | 15            | 1   | 50     | '1'   | [1, 0, 1]    | [12, 35, 41] |
| 40   | 41             | 40            | 20            | 1   | 35     | '2'   | [1, 0, 1]    | [48, 50, 55] |



In [1]:
import pandas as pd
import numpy as np
import numpy.random as random
from route_functions import *
import matplotlib.pyplot as plt

In [69]:
def fleet_simulation(t, T, routes, buses, refuel, running_consumption, service_consumption, 
                     refuel_stations, refuel_consumption, conversion_factor,
                     demand_at, demand_ct, demand_r, demand_c, dct_flag, SS_cols, BD_cols):
    ss_table = pd.DataFrame(columns=SS_cols)
    bd_table = pd.DataFrame(columns=BD_cols)

    # Initial SS update
    time_check = np.inf
    ss_table = SS_update(ss_table, t, buses, dct_flag, np.nan, np.nan)
    
    # previous times for fleet
    prev_time = [np.nan]*len(buses)
    
    # Simulate! Simulate! Simulate!        
    while (t<T)or(time_check!=np.inf):
        print('\n---\nNew Loop')

        time_check = min(next_bus_e(buses)[0], demand_ct[0])
        print('Time check -', time_check)

        # -----
        # Priority One: Updating demands
        if ((demand_ct[0]!=np.inf) and
            (demand_ct[0]==time_check)):
            new_demand = [1 for i in range(len(demand_ct)) if demand_ct[i]==time_check]
            dct_flag = sum(new_demand)
            
            # testing
            t = time_check
            
        print('\tDemands -', demand_ct[:10], demand_at[:10], demand_r[:10], demand_c[:10])
        print('\tdct_flag -', dct_flag)


        #----------
        # Main Simulation
        bus_chk = available_bus(buses, demand_c[0])
        print('Bus Check -', bus_chk)


        #-----
        # Case 1: Sending low-fuel buses to refuel
        refuel_index = unavailable_bus(buses, min(demand_c))
        if (#(t<T) and
            (refuel_index!=-1) and
            (buses_status(buses)[1]<refuel_stations)): 
            # or((dct_flag>0)and(refuel_index!=np.inf)):- might create complications
            dem_ct, dem_at, dem_c = np.nan, np.nan, np.nan
            print('Sending Bus for Refuel')
            buses[refuel_index].assign_route(routes, refuel, t)
            prev_time[refuel_index] = t
            bus_e = 0
            t_updt = t

            ss_table = SS_update(ss_table, t, buses, dct_flag, bus_e, t_updt, refuel_index)
            bd_table = BD_update(bd_table, t_updt, dem_ct, dem_at, dem_c, buses, refuel_index)

            t = t_updt
            #refuel_index = -1


        #-----
        # Case 2: Checking bus availability and deploying buses
        elif ((t<T) and
              (demand_ct[0]==time_check) and
              (demand_ct[0]!=np.inf) and
              (bus_chk!=-1)):

            print('Deploying Bus')
            dem_ct, dem_at = demand_ct.pop(0), demand_at.pop(0)
            dem_c, dem_r = demand_c.pop(0), demand_r.pop(0)
            index = available_bus(buses, dem_c)
            t_updt = dem_ct
            buses[index].assign_route(routes, dem_r, t_updt)
            prev_time[index] = t_updt
            bus_e = 0

            ss_table = SS_update(ss_table, t, buses, dct_flag, bus_e, t_updt, index, dem_ct, dem_at, dem_c)
            bd_table = BD_update(bd_table, t_updt, dem_ct, dem_at, dem_c, buses, index)
            print(buses[index].event_arr, buses[index].time_arr)
            dct_flag -= 1
            print(prev_time[index], t_updt)
            t = t_updt

            dem_ct, dem_at, dem_c, dem_r = np.nan, np.nan, np.nan, np.nan
            t_updt = np.nan
            index = np.nan


        #-----
        # Case 3: Checking next bus event and updating SS
        elif ((t<T) and
              (next_bus_e(buses)[0]==time_check) and 
              (next_bus_e(buses)[0]!=np.inf) and 
              ((buses_status(buses)[0]>0) or (buses_status(buses)[1]>0))):

            print('Updating next bus event')
            index = next_bus_e(buses)[2]
            t_updt = buses[index].time_arr.pop(0)
            bus_e = buses[index].event_arr.pop(0)
            diff_t = prev_time[index]
            
            if (bus_e==1):
                mul_c = running_consumption
            elif (bus_e==0)and(buses[index].state==1):
                mul_c = service_consumption
            elif (bus_e==0)and(buses[index].state==0):                       # different for 'refill' and 'recharge' 
                mul_c = refuel_consumption                                   # difference from 90 for refill
            buses[index].charge = round(buses[index].charge - (t_updt - diff_t)*mul_c*conversion_factor, 3)

            ss_table = SS_update(ss_table, t, buses, dct_flag, bus_e, t_updt, index)
            t = t_updt
            prev_time[index] = t
            
            # if its the last event for the bus, update bus parameters to standstill
            if buses[index].next_e()==np.inf:
                buses[index].state = -1
                buses[index].route = None
                buses[index].time_arr = list()
                buses[index].event_arr = list()
                prev_time[index] = np.nan
            index = np.nan
            t_updt = np.nan
            bus_e = np.nan
        
        
        #-----
        # Case 4: Jumping to next demand 
        elif ((t<T) and
              (demand_ct[0]==time_check) and 
              (demand_ct[0]!=np.inf) and 
              (bus_chk==-1)):
            t = demand_ct[dct_flag].copy()
            #dct_flag += 1
        
              
        #-----
        # Case 5: All demands are completed within the timeframe 
        elif ((t<T) and
              (time_check==np.inf)):

            print('Jumping to EOD')
            t_updt = T

            ss_table = SS_update(ss_table, t, buses, dct_flag, bus_e, t_updt)
            t = t_updt    


        #-----
        # Case 6: Demands still exist beyond timeframe and need to be met
        elif ((t>T) and
              (demand_ct[0]==time_check) and
              (demand_ct[0]!=np.inf) and
              (bus_chk!=-1)):

            print('Deploying Bus beyond timeframe')
            dem_ct, dem_at = demand_ct.pop(0), demand_at.pop(0)
            dem_c, dem_r = demand_c.pop(0), demand_r.pop(0)
            index = available_bus(buses, dem_c)
            t_updt = dem_ct
            buses[index].assign_route(routes, dem_r, t_updt)
            prev_time[index] = t_updt
            bus_e = 0

            ss_table = SS_update(ss_table, t, buses, dct_flag, bus_e, t_updt, index, dem_ct, dem_at, dem_c)
            bd_table = BD_update(bd_table, t_updt, dem_ct, dem_at, dem_c, buses, index)
            dct_flag -= 1
            t = t_updt

            dem_ct, dem_at, dem_c, dem_r = np.nan, np.nan, np.nan, np.nan
            t_updt = np.nan
            index = np.nan


        #-----
        # Case 7: Going beyond timeframe, checking deployed buses and updating SS
        elif (((t>T) and
              (next_bus_e(buses)[0]==time_check) and
              (next_bus_e(buses)[0]!=np.inf)) or
              ((t>T) and
              (demand_ct[0]==time_check) and 
              (demand_ct[0]!=np.inf) and 
              (bus_chk==-1))):
            
            print('Updating next bus event beyond timeframe')
            index = next_bus_e(buses)[2]
            t_updt = buses[index].time_arr.pop(0)
            bus_e = buses[index].event_arr.pop(0)
            diff_t = prev_time[index]
            
            if (bus_e==1):
                mul_c = running_consumption
            elif (bus_e==0)and(buses[index].state==1):
                mul_c = service_consumption
            elif (bus_e==0)and(buses[index].state==0):                       # different for 'refill' and 'recharge' 
                mul_c = refuel_consumption                                   # difference from 90 for refill
            buses[index].charge = buses[index].charge - (t_updt - diff_t)*mul_c*conversion_factor

            ss_table = SS_update(ss_table, t, buses, dct_flag, bus_e, t_updt, index)
            t = t_updt
            prev_time[index] = t
            
            # if its the last event for the bus, update bus parameters to standstill
            if buses[index].next_e()==np.inf:
                buses[index].state = -1
                buses[index].route = None
                buses[index].time_arr = list()
                buses[index].event_arr = list()
                prev_time[index] = np.nan
            index = np.nan
            t_updt = np.nan
            bus_e = np.nan

        #-----
        # Case 8: All demands are completed outside the timeframe 
        elif ((t>T) and
              (time_check==np.inf)):

            print('Jumping to EOD')
            t_updt = np.inf        
            ss_table = SS_update(ss_table, t, buses, dct_flag, bus_e, t_updt)
            t = t_updt    



        print('\tDemands -', demand_ct[:10], demand_at[:10], demand_r[:10], demand_c[:10])
        print('\tdct_flag -', dct_flag)

        # updating the current demand - if demand exists it'll automatically be updated
        for k in range(dct_flag):
            demand_ct[k] = t
        
        #checking alternative
        #if (refuel_index!=-1):
        #    refuel_index = -1
        #else:
        #    for k in range(dct_flag):
        #        demand_ct[k] = t
            
        
        
        print('\tDemands -', demand_ct[:10], demand_at[:10], demand_r[:10], demand_c[:10])
        print('\tdct_flag -', dct_flag)
        print('t -', t)
    
    return ss_table, bd_table

In [70]:
# intializing route table
routes = pd.read_excel('Model_Parameters.xlsx', 'Routes')

# customizable parameters
#average_bus_speed = 10
running_consumption = 0.09             # fuel(lts.)/kWh per minute
service_consumption = 0.07 
refuel_stations = 2
refuel_consumption = -30
tank_size = 250
conversion_factor = 100/tank_size


# tank level/charge of buses
level_mean = 50       # normal distribution.. can be changed
level_std = 2.5
refuel = 'refill'     # 'recharge'

# setting up initial values for simulation
n_buses = 6                                # number of buses
n_routes = 2                               # number of routes
buses = [bus(level_mean, level_std) for i in range(n_buses)]    # fleet of buses
SimTime = 720*10

# updating demands
demand_at, demand_r, demand_c = gen_demands(n_routes, SimTime)
demand_ct = demand_at.copy()               # demand current time and demand actual time
dct_flag = 0                               # demand at current time

'''# -----
#### creating fake data & demands
t = 0                                      # start time of simulation
T = 60
buses = [bus(5, 5) for i in range(1)]
demand_at = [0, 40, np.inf]
demand_r = ['1', '2', None]
demand_c = [15, 20, np.inf]
demand_ct = demand_at.copy()         # demand current time and demand actual time
dct_flag = 0                  # demand at current time'''

SS_cols = ['Time', 'System_State', 'Bus', 'Charge', 'Route', 
           'State', 'Event', 'Process_Time', 'Demand_Current', 
           'Demand_Actual', 'Demand_Charge']
BD_cols = ['Time', 'Demand_Current', 'Demand_Actual', 'Demand_Charge', 
           'Bus', 'Charge', 'Route', 'Event_Array', 'Time_Array']
  

In [71]:
replicates = 1
ss_table = pd.DataFrame(columns=SS_cols+['Replication'])
bd_table = pd.DataFrame(columns=BD_cols+['Replication'])

for i in range(replicates):
    print('\n\n-----\n-----\nNEW SIMULATION')
    # intializing required variabes
    buses = [bus(level_mean, level_std) for i in range(n_buses)]    # fleet of buses
    t = 0                                      # start time of simulation
    T = SimTime

    # updating demands
    demand_at, demand_r, demand_c = gen_demands(n_routes, T)
    demand_ct = demand_at.copy()         # demand current time and demand actual time
    dct_flag = 0                         # demand at current time

    ss_tab, bd_tab = fleet_simulation(t, T, routes, buses, refuel, running_consumption, 
                                      service_consumption, refuel_stations, refuel_consumption, conversion_factor,
                                      demand_at, demand_ct, demand_r, demand_c, dct_flag, SS_cols, BD_cols)
    ss_tab['Replication'] = i+1
    bd_tab['Replication'] = i+1
    ss_table = ss_table.append(ss_tab, ignore_index=True)
    bd_table = bd_table.append(bd_tab, ignore_index=True)



-----
-----
NEW SIMULATION

---
New Loop
Time check - 0.0
	Demands - [0.0, 0.0, 30.0, 30.0, 60.0, 60.0, 72.0, 84.0, 90.0, 96.0] [0.0, 0.0, 30.0, 30.0, 60.0, 60.0, 72.0, 84.0, 90.0, 96.0] ['1', '2', '1', '2', '1', '2', '1', '1', '2', '1'] [25.0, 25.0, 25.0, 25.0, 25.0, 25.0, 25.0, 25.0, 25.0, 25.0]
	dct_flag - 2
Bus Check - 1
Deploying Bus
[1, 0, 1, 0, 1, 0, 1] [5.31, 5.64, 20.69, 21.78, 27.04, 30.91, 38.03]
0.0 0.0
	Demands - [0.0, 30.0, 30.0, 60.0, 60.0, 72.0, 84.0, 90.0, 96.0, 108.0] [0.0, 30.0, 30.0, 60.0, 60.0, 72.0, 84.0, 90.0, 96.0, 108.0] ['2', '1', '2', '1', '2', '1', '1', '2', '1', '1'] [25.0, 25.0, 25.0, 25.0, 25.0, 25.0, 25.0, 25.0, 25.0, 25.0]
	dct_flag - 1
	Demands - [0.0, 30.0, 30.0, 60.0, 60.0, 72.0, 84.0, 90.0, 96.0, 108.0] [0.0, 30.0, 30.0, 60.0, 60.0, 72.0, 84.0, 90.0, 96.0, 108.0] ['2', '1', '2', '1', '2', '1', '1', '2', '1', '1'] [25.0, 25.0, 25.0, 25.0, 25.0, 25.0, 25.0, 25.0, 25.0, 25.0]
	dct_flag - 1
t - 0.0

---
New Loop
Time check - 0.0
	Demands - [0.0, 30.0,

C:\Users\krishrao\Anaconda3\lib\site-packages\pandas\util\_decorators.py:311: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  return func(*args, **kwargs)


 [30.0, 30.0, 60.0, 60.0, 72.0, 84.0, 90.0, 96.0, 108.0, 120.0] [30.0, 30.0, 60.0, 60.0, 72.0, 84.0, 90.0, 96.0, 108.0, 120.0] ['1', '2', '1', '2', '1', '1', '2', '1', '1', '1'] [25.0, 25.0, 25.0, 25.0, 25.0, 25.0, 25.0, 25.0, 25.0, 25.0]
	dct_flag - 0
	Demands - [30.0, 30.0, 60.0, 60.0, 72.0, 84.0, 90.0, 96.0, 108.0, 120.0] [30.0, 30.0, 60.0, 60.0, 72.0, 84.0, 90.0, 96.0, 108.0, 120.0] ['1', '2', '1', '2', '1', '1', '2', '1', '1', '1'] [25.0, 25.0, 25.0, 25.0, 25.0, 25.0, 25.0, 25.0, 25.0, 25.0]
	dct_flag - 0
t - 20.69

---
New Loop
Time check - 21.78
	Demands - [30.0, 30.0, 60.0, 60.0, 72.0, 84.0, 90.0, 96.0, 108.0, 120.0] [30.0, 30.0, 60.0, 60.0, 72.0, 84.0, 90.0, 96.0, 108.0, 120.0] ['1', '2', '1', '2', '1', '1', '2', '1', '1', '1'] [25.0, 25.0, 25.0, 25.0, 25.0, 25.0, 25.0, 25.0, 25.0, 25.0]
	dct_flag - 0
Bus Check - 5
Updating next bus event
	Demands - [30.0, 30.0, 60.0, 60.0, 72.0, 84.0, 90.0, 96.0, 108.0, 120.0] [30.0, 30.0, 60.0, 60.0, 72.0, 84.0, 90.0, 96.0, 108.0, 120.0] ['1

	Demands - [60.0, 60.0, 72.0, 84.0, 90.0, 96.0, 108.0, 120.0, 120.0, 132.0] [60.0, 60.0, 72.0, 84.0, 90.0, 96.0, 108.0, 120.0, 120.0, 132.0] ['1', '2', '1', '1', '2', '1', '1', '1', '2', '1'] [25.0, 25.0, 25.0, 25.0, 25.0, 25.0, 25.0, 25.0, 25.0, 25.0]
	dct_flag - 0
Bus Check - 1
Updating next bus event
	Demands - [60.0, 60.0, 72.0, 84.0, 90.0, 96.0, 108.0, 120.0, 120.0, 132.0] [60.0, 60.0, 72.0, 84.0, 90.0, 96.0, 108.0, 120.0, 120.0, 132.0] ['1', '2', '1', '1', '2', '1', '1', '1', '2', '1'] [25.0, 25.0, 25.0, 25.0, 25.0, 25.0, 25.0, 25.0, 25.0, 25.0]
	dct_flag - 0
	Demands - [60.0, 60.0, 72.0, 84.0, 90.0, 96.0, 108.0, 120.0, 120.0, 132.0] [60.0, 60.0, 72.0, 84.0, 90.0, 96.0, 108.0, 120.0, 120.0, 132.0] ['1', '2', '1', '1', '2', '1', '1', '1', '2', '1'] [25.0, 25.0, 25.0, 25.0, 25.0, 25.0, 25.0, 25.0, 25.0, 25.0]
	dct_flag - 0
t - 46.42

---
New Loop
Time check - 48.69
	Demands - [60.0, 60.0, 72.0, 84.0, 90.0, 96.0, 108.0, 120.0, 120.0, 132.0] [60.0, 60.0, 72.0, 84.0, 90.0, 96.0, 108.0

	Demands - [72.0, 84.0, 90.0, 96.0, 108.0, 120.0, 120.0, 132.0, 140.0, 144.0] [72.0, 84.0, 90.0, 96.0, 108.0, 120.0, 120.0, 132.0, 140.0, 144.0] ['1', '1', '2', '1', '1', '1', '2', '1', '2', '1'] [25.0, 25.0, 25.0, 25.0, 25.0, 25.0, 25.0, 25.0, 25.0, 25.0]
	dct_flag - 0
	Demands - [72.0, 84.0, 90.0, 96.0, 108.0, 120.0, 120.0, 132.0, 140.0, 144.0] [72.0, 84.0, 90.0, 96.0, 108.0, 120.0, 120.0, 132.0, 140.0, 144.0] ['1', '1', '2', '1', '1', '1', '2', '1', '2', '1'] [25.0, 25.0, 25.0, 25.0, 25.0, 25.0, 25.0, 25.0, 25.0, 25.0]
	dct_flag - 0
t - 67.5

---
New Loop
Time check - 67.64
	Demands - [72.0, 84.0, 90.0, 96.0, 108.0, 120.0, 120.0, 132.0, 140.0, 144.0] [72.0, 84.0, 90.0, 96.0, 108.0, 120.0, 120.0, 132.0, 140.0, 144.0] ['1', '1', '2', '1', '1', '1', '2', '1', '2', '1'] [25.0, 25.0, 25.0, 25.0, 25.0, 25.0, 25.0, 25.0, 25.0, 25.0]
	dct_flag - 0
Bus Check - 5
Updating next bus event
	Demands - [72.0, 84.0, 90.0, 96.0, 108.0, 120.0, 120.0, 132.0, 140.0, 144.0] [72.0, 84.0, 90.0, 96.0, 108.

...

[1, 0, 1, 0, 1, 0, 1] [7146.87, 7146.97, 7156.63, 7158.34, 7161.27, 7162.94, 7175.72]
7140.0 7140.0
	Demands - [7140.0, 7152.0, 7152.0, 7164.0, 7164.0, 7176.0, 7176.0, 7188.0, 7188.0, inf] [7140.0, 7152.0, 7152.0, 7164.0, 7164.0, 7176.0, 7176.0, 7188.0, 7188.0, inf] ['2', '1', '2', '1', '2', '1', '2', '1', '2', None] [25.0, 25.0, 25.0, 25.0, 25.0, 25.0, 25.0, 25.0, 25.0, inf]
	dct_flag - 1
	Demands - [7140.0, 7152.0, 7152.0, 7164.0, 7164.0, 7176.0, 7176.0, 7188.0, 7188.0, inf] [7140.0, 7152.0, 7152.0, 7164.0, 7164.0, 7176.0, 7176.0, 7188.0, 7188.0, inf] ['2', '1', '2', '1', '2', '1', '2', '1', '2', None] [25.0, 25.0, 25.0, 25.0, 25.0, 25.0, 25.0, 25.0, 25.0, inf]
	dct_flag - 1
t - 7140.0

---
New Loop
Time check - 7140.0
	Demands - [7140.0, 7152.0, 7152.0, 7164.0, 7164.0, 7176.0, 7176.0, 7188.0, 7188.0, inf] [7140.0, 7152.0, 7152.0, 7164.0, 7164.0, 7176.0, 7176.0, 7188.0, 7188.0, inf] ['2', '1', '2', '1', '2', '1', '2', '1', '2', None] [25.0, 25.0, 25.0, 25.0, 25.0, 25.0, 25.0, 25.0, 2

	Demands - [7152.0, 7152.0, 7164.0, 7164.0, 7176.0, 7176.0, 7188.0, 7188.0, inf] [7152.0, 7152.0, 7164.0, 7164.0, 7176.0, 7176.0, 7188.0, 7188.0, inf] ['1', '2', '1', '2', '1', '2', '1', '2', None] [25.0, 25.0, 25.0, 25.0, 25.0, 25.0, 25.0, 25.0, inf]
	dct_flag - 0
t - 7146.9

---
New Loop
Time check - 7146.97
	Demands - [7152.0, 7152.0, 7164.0, 7164.0, 7176.0, 7176.0, 7188.0, 7188.0, inf] [7152.0, 7152.0, 7164.0, 7164.0, 7176.0, 7176.0, 7188.0, 7188.0, inf] ['1', '2', '1', '2', '1', '2', '1', '2', None] [25.0, 25.0, 25.0, 25.0, 25.0, 25.0, 25.0, 25.0, inf]
	dct_flag - 0
Bus Check - 0
Updating next bus event
	Demands - [7152.0, 7152.0, 7164.0, 7164.0, 7176.0, 7176.0, 7188.0, 7188.0, inf] [7152.0, 7152.0, 7164.0, 7164.0, 7176.0, 7176.0, 7188.0, 7188.0, inf] ['1', '2', '1', '2', '1', '2', '1', '2', None] [25.0, 25.0, 25.0, 25.0, 25.0, 25.0, 25.0, 25.0, inf]
	dct_flag - 0
	Demands - [7152.0, 7152.0, 7164.0, 7164.0, 7176.0, 7176.0, 7188.0, 7188.0, inf] [7152.0, 7152.0, 7164.0, 7164.0, 7176

	Demands - [7164.0, 7164.0, 7176.0, 7176.0, 7188.0, 7188.0, inf] [7164.0, 7164.0, 7176.0, 7176.0, 7188.0, 7188.0, inf] ['1', '2', '1', '2', '1', '2', None] [25.0, 25.0, 25.0, 25.0, 25.0, 25.0, inf]
	dct_flag - 0
	Demands - [7164.0, 7164.0, 7176.0, 7176.0, 7188.0, 7188.0, inf] [7164.0, 7164.0, 7176.0, 7176.0, 7188.0, 7188.0, inf] ['1', '2', '1', '2', '1', '2', None] [25.0, 25.0, 25.0, 25.0, 25.0, 25.0, inf]
	dct_flag - 0
t - 7159.71

---
New Loop
Time check - 7161.27
	Demands - [7164.0, 7164.0, 7176.0, 7176.0, 7188.0, 7188.0, inf] [7164.0, 7164.0, 7176.0, 7176.0, 7188.0, 7188.0, inf] ['1', '2', '1', '2', '1', '2', None] [25.0, 25.0, 25.0, 25.0, 25.0, 25.0, inf]
	dct_flag - 0
Bus Check - 3
Updating next bus event
	Demands - [7164.0, 7164.0, 7176.0, 7176.0, 7188.0, 7188.0, inf] [7164.0, 7164.0, 7176.0, 7176.0, 7188.0, 7188.0, inf] ['1', '2', '1', '2', '1', '2', None] [25.0, 25.0, 25.0, 25.0, 25.0, 25.0, inf]
	dct_flag - 0
	Demands - [7164.0, 7164.0, 7176.0, 7176.0, 7188.0, 7188.0, inf] [7

	Demands - [7188.0, 7188.0, inf] [7188.0, 7188.0, inf] ['1', '2', None] [25.0, 25.0, inf]
	dct_flag - 0
	Demands - [7188.0, 7188.0, inf] [7188.0, 7188.0, inf] ['1', '2', None] [25.0, 25.0, inf]
	dct_flag - 0
t - 7180.14

---
New Loop
Time check - 7180.32
	Demands - [7188.0, 7188.0, inf] [7188.0, 7188.0, inf] ['1', '2', None] [25.0, 25.0, inf]
	dct_flag - 0
Bus Check - 5
Updating next bus event
	Demands - [7188.0, 7188.0, inf] [7188.0, 7188.0, inf] ['1', '2', None] [25.0, 25.0, inf]
	dct_flag - 0
	Demands - [7188.0, 7188.0, inf] [7188.0, 7188.0, inf] ['1', '2', None] [25.0, 25.0, inf]
	dct_flag - 0
t - 7180.32

---
New Loop
Time check - 7181.12
	Demands - [7188.0, 7188.0, inf] [7188.0, 7188.0, inf] ['1', '2', None] [25.0, 25.0, inf]
	dct_flag - 0
Bus Check - 5
Updating next bus event
	Demands - [7188.0, 7188.0, inf] [7188.0, 7188.0, inf] ['1', '2', None] [25.0, 25.0, inf]
	dct_flag - 0
	Demands - [7188.0, 7188.0, inf] [7188.0, 7188.0, inf] ['1', '2', None] [25.0, 25.0, inf]
	dct_flag - 

	Demands - [inf] [inf] [None] [inf]
	dct_flag - 0
	Demands - [inf] [inf] [None] [inf]
	dct_flag - 0
t - inf


In [84]:
ss_tab[:50]

Time     System_State  Bus     Charge Route State Event  Process_Time  \
0     NaN  [6, 0, 0, 0, 6]  NaN        NaN  None   NaN   NaN           NaN   
1    0.00  [6, 2, 1, 0, 5]    2  51.905257     1     1     0          0.00   
2    0.00  [6, 1, 2, 0, 4]    6  50.790049     2     1     0          0.00   
3    2.75  [6, 0, 2, 0, 4]    6  50.666299     2     1   1.0          2.75   
4    3.73  [6, 0, 2, 0, 4]    6  50.629549     2     1   0.0          0.98   
5    5.31  [6, 0, 2, 0, 4]    2  51.666307     1     1     1          1.58   
6    5.64  [6, 0, 2, 0, 4]    2  51.653932     1     1     0          0.33   
7   14.52  [6, 0, 2, 0, 4]    6  50.143999     2     1   1.0          8.88   
8   14.87  [6, 0, 2, 0, 4]    6  50.130874     2     1   0.0          0.35   
9   19.19  [6, 0, 2, 0, 4]    6  49.936474     2     1   1.0          4.32   
10  20.69  [6, 0, 1, 0, 5]    2  50.976682     1     1     1          1.50   
11  21.78  [6, 0, 1, 0, 5]    2  50.935807     1     1     0          1.09   
12  27.04  [6, 0, 1, 0, 5]    2  50.699107     1     1     1          5.26   
13  30.00  [6, 2, 2, 0, 4]    6  49.936474     1     1     0          0.00   
14  30.00  [6, 1, 3, 0, 3]    1  49.339203     2     1     0          0.00   
15  30.91  [6, 0, 3, 0, 3]    2  50.553982     1     1     0          0.91   
16  34.50  [6, 0, 3, 0, 3]    6  49.733974     1     1     1          3.59   
17  34.95  [6, 0, 3, 0, 3]    6  49.717099     1     1     0          0.45   
18  35.26  [6, 0, 3, 0, 3]    1  49.102503     2     1   1.0          0.31   
19  35.28  [6, 0, 3, 0, 3]    1  49.101753     2     1   0.0          0.02   
20  38.03  [6, 0, 3, 0, 3]    2  50.233582     1     1     1          2.75   
21  46.10  [6, 0, 2, 0, 4]    1  48.614853     2     1   1.0          8.07   
22  46.42  [6, 0, 2, 0, 4]    1  48.602853     2     1   0.0          0.32   
23  48.69  [6, 0, 2, 0, 4]    6  49.098799     1     1     1          2.27   
24  49.08  [6, 0, 2, 0, 4]    6  49.084174     1     1     0          0.39   
25  52.04  [6, 0, 2, 0, 4]    1  48.349953     2     1   1.0          2.96   
26  58.33  [6, 0, 1, 0, 5]    6  48.667924     1     1     1          6.29   
27  58.91  [6, 0, 1, 0, 5]    6  48.646174     1     1     0          0.58   
28  60.00  [6, 2, 2, 0, 4]    2  50.233582     1     1     0          0.00   
29  60.00  [6, 1, 3, 0, 3]    1  48.349953     2     1     0          0.00   
30  66.32  [6, 0, 3, 0, 3]    2  49.949182     1     1     1          6.32   
31  67.50  [6, 0, 3, 0, 3]    6  48.259624     1     1     1          1.18   
32  67.64  [6, 0, 2, 0, 4]    2  49.899682     1     1     0          0.14   
33  67.90  [6, 0, 2, 0, 4]    1  47.994453     2     1   1.0          0.26   
34  68.56  [6, 0, 2, 0, 4]    1  47.969703     2     1   0.0          0.66   
35  72.00  [6, 1, 3, 0, 3]    6  48.259624     1     1     0          0.00   
36  75.50  [6, 0, 3, 0, 3]    6  48.102124     1     1     1          3.50   
37  76.51  [6, 0, 3, 0, 3]    6  48.064249     1     1     0          1.01   
38  77.05  [6, 0, 3, 0, 3]    1  47.587653     2     1   1.0          0.54   
39  78.20  [6, 0, 3, 0, 3]    2  49.424482     1     1     1          1.15   
40  79.01  [6, 0, 3, 0, 3]    1  47.514153     2     1   0.0          0.81   
41  79.40  [6, 0, 3, 0, 3]    2  49.379482     1     1     0          0.39   
42  82.10  [6, 0, 3, 0, 3]    1  47.375103     2     1   1.0          2.70   
43  84.00  [6, 1, 3, 0, 3]    4  47.980115     1     1     0          0.00   
44  87.71  [6, 0, 3, 0, 3]    2  49.005532     1     1     1          3.71   
45  88.06  [6, 0, 3, 0, 3]    2  48.992407     1     1     0          0.35   
46  88.10  [6, 0, 3, 0, 3]    4  47.795615     1     1     1          0.04   
47  88.20  [6, 0, 3, 0, 3]    4  47.791865     1     1     0          0.10   
48  90.00  [6, 1, 4, 0, 2]    1  47.375103     2     1     0          0.00   
49  90.62  [6, 0, 4, 0, 2]    6  47.429299     1     1     1          0.62   

    Demand_Current  Demand

In [73]:
bd_tab

Time  Demand_Current  Demand_Actual  Demand_Charge Bus     Charge  \
0       0.0             0.0            0.0           25.0   2  51.905257   
1       0.0             0.0            0.0           25.0   6  50.790049   
2      30.0            30.0           30.0           25.0   6  49.936474   
3      30.0            30.0           30.0           25.0   1  49.339203   
4      60.0            60.0           60.0           25.0   2  50.233582   
..      ...             ...            ...            ...  ..        ...   
764  7164.0          7164.0         7164.0           25.0   2  28.387207   
765  7176.0          7176.0         7176.0           25.0   3  26.319215   
766  7176.0          7176.0         7176.0           25.0   5  26.216317   
767  7188.0          7188.0         7188.0           25.0   2  27.377932   
768  7188.0          7188.0         7188.0           25.0   6  26.166274   

    Route                Event_Array  \
0       1      [1, 0, 1, 0, 1, 0, 1]   
1       2  [1.0, 0.0, 1.0, 0.0, 1.0]   
2       1      [1, 0, 1, 0, 1, 0, 1]   
3       2  [1.0, 0.0, 1.0, 0.0, 1.0]   
4       1      [1, 0, 1, 0, 1, 0, 1]   
..    ...                        ...   
764     2  [1.0, 0.0, 1.0, 0.0, 1.0]   
765     1      [1, 0, 1, 0, 1, 0, 1]   
766     2  [1.0, 0.0, 1.0, 0.0, 1.0]   
767     1      [1, 0, 1, 0, 1, 0, 1]   
768     2  [1.0, 0.0, 1.0, 0.0, 1.0]   

                                            Time_Array  State  Replication  
0      [5.31, 5.64, 20.69, 21.78, 27.04, 30.91, 38.03]    1.0            1  
1                    [2.75, 3.73, 14.52, 14.87, 19.19]    1.0            1  
2      [34.5, 34.95, 48.69, 49.08, 58.33, 58.91, 67.5]    1.0            1  
3                   [35.26, 35.28, 46.1, 46.42, 52.04]    1.0            1  
4       [66.32, 67.64, 78.2, 79.4, 87.71, 88.06, 96.7]    1.0            1  
..                                                 ...    ...          ...  
764      [7168.13, 7168.18, 7181.12, 7181.44, 7186.49]    1.0            1  
765  [7183.16, 7183.41, 7194.21, 7194.9, 7199.63, 7...    1.0            1  
766      [7179.72, 7180.14, 7207.94, 7208.03, 7213.24]    1.0            1  
767  [7191.8, 7191.88, 7202.78, 7203.92, 7214.03, 7...    1.0            1  
768      [7190.88, 7190.98, 7205.98, 7207.27, 7215.34]    1.0            1  

[769 rows x 11 columns]

In [74]:
ss_table[:100]

Time     System_State  Bus     Charge Route State Event  Process_Time  \
0      NaN  [6, 0, 0, 0, 6]  NaN        NaN  None   NaN   NaN           NaN   
1     0.00  [6, 2, 1, 0, 5]    2  51.905257     1     1     0          0.00   
2     0.00  [6, 1, 2, 0, 4]    6  50.790049     2     1     0          0.00   
3     2.75  [6, 0, 2, 0, 4]    6  50.666299     2     1   1.0          2.75   
4     3.73  [6, 0, 2, 0, 4]    6  50.629549     2     1   0.0          0.98   
..     ...              ...  ...        ...   ...   ...   ...           ...   
95  143.36  [6, 0, 5, 0, 1]    5  44.113717     1     1     1          1.59   
96  143.73  [6, 0, 4, 0, 2]    6  45.478549     1     1     0          0.37   
97  144.00  [6, 1, 5, 0, 1]    5  44.113717     1     1     0          0.00   
98  145.26  [6, 0, 5, 0, 1]    2  46.938607     1     1     1          1.26   
99  147.10  [6, 0, 4, 0, 2]    5  43.974217     1     1     1          1.84   

    Demand_Current  Demand_Actual  Demand_Charge Replication  
0              NaN            NaN            NaN           1  
1              0.0            0.0           25.0           1  
2              0.0            0.0           25.0           1  
3              NaN            NaN            NaN           1  
4              NaN            NaN            NaN           1  
..             ...            ...            ...         ...  
95             NaN            NaN            NaN           1  
96             NaN            NaN            NaN           1  
97           144.0          144.0           25.0           1  
98             NaN            NaN            NaN           1  
99             NaN            NaN            NaN           1  

[100 rows x 12 columns]

In [91]:
bd_table[(bd_table['Bus']==2)&(bd_table['Route']=='refill')]

Time  Demand_Current  Demand_Actual  Demand_Charge Bus     Charge  \
102  1032.00             NaN            NaN            NaN   2  24.377707   
170  1585.95             NaN            NaN            NaN   2  24.609307   
289  2653.22             NaN            NaN            NaN   2  24.320182   
424  3978.41             NaN            NaN            NaN   2  24.893407   
508  4807.25             NaN            NaN            NaN   2  24.833107   
607  5679.11             NaN            NaN            NaN   2  23.990707   
676  6331.70             NaN            NaN            NaN   2  24.799882   

      Route      Event_Array                   Time_Array Replication  State  
102  refill  [1.0, 0.0, 1.0]  [1032.19, 1033.14, 1034.02]           1    0.0  
170  refill  [1.0, 0.0, 1.0]  [1586.23, 1588.78, 1589.43]           1    0.0  
289  refill  [1.0, 0.0, 1.0]  [2653.28, 2655.64, 2658.07]           1    0.0  
424  refill  [1.0, 0.0, 1.0]  [3978.66, 3979.84, 3980.69]           1    0.0  
508  refill  [1.0, 0.0, 1.0]  [4807.54, 4808.53, 4809.89]           1    0.0  
607  refill  [1.0, 0.0, 1.0]  [5679.74, 5680.57, 5681.42]           1    0.0  
676  refill  [1.0, 0.0, 1.0]  [6332.21, 6334.45, 6334.66]           1    0.0

___
## Model Analysis

In [76]:
# delay analysis on deployments
num_delay = sum(np.array(bd_table['Demand_Current'] - bd_table['Demand_Actual'])>0)
total_delay = sum(np.nan_to_num(np.array(bd_table['Demand_Current'] - bd_table['Demand_Actual'])))
avg_delay = np.mean(np.nan_to_num(np.array(bd_table['Demand_Current'] - bd_table['Demand_Actual'])))

num_delay, round(total_delay, 2), round(total_delay, 2)/num_delay, round(avg_delay, 2)

(46, 204.02, 4.435217391304348, 0.27)

In [77]:
sum(bd_table['Route']!='refill')

722

In [78]:
sum(bd_table['Route']=='refill')

47

In [79]:
# Charge distribution
ss_table['Charge'].min(), ss_table['Charge'].max()

(23.25561465380971, 63.69259898125064)

___
## Testing Area

In [13]:
demand_at, demand_r, demand_c = gen_demands(2, 240)
np.array(demand_at)

array([  0.,   0.,  30.,  30.,  60.,  60.,  72.,  84.,  90.,  96., 108.,
       120., 120., 132., 140., 144., 156., 160., 168., 180., 180., 192.,
       200., 204., 216., 220., 228.,  inf])

In [14]:
# testing for demand creation and updation

#demand = 0
arr = [0, 1, 0, 1, 2, 3]
test = 5
new_demand = [1 for i in range(len(arr)) if arr[i]==test]
demand = demand + sum(new_demand)
demand

NameError: name 'demand' is not defined

In [ ]:
routes[routes.columns[routes.columns.str.match('route_1')]]

In [ ]:
print(route_time(routes, 'recharge', 0))
print(route_time(routes, 'refill', 0))
print(route_time(routes, '2', 0))

In [ ]:
n_buses = 4
buses = [bus(50, 5) for i in range(n_buses)]
t = 10
buses[0].assign_route(routes, 'refill', t)
buses[1].assign_route(routes, '1', t)
buses[2].assign_route(routes, '1', t)
print(buses[0].time_arr)
print(buses[0].event_arr)
buses_status(buses)

In [ ]:
print(buses[0].next_t())
print(buses[0].next_e())
print(buses[0].time_arr.pop(0))
print(buses[0].event_arr.pop(0))
print(buses[0].next_t())
print(buses[0].next_e())

In [ ]:
#### ASSUMPTION: buses are prioritized based on their index

def next_bus_e(buses):
    min_t = np.inf
    index = None
    for i in range(len(buses)):
        print(buses[i].next_t())
        if (buses[i].next_t()<min_t):
            min_t = buses[i].next_t()
            index = i
    return min_t, buses[i].next_e(), index

# testing 
buses = [bus(50, 5) for i in range(3)]
buses[0].assign_route(routes, '1', 0)
buses[1].assign_route(routes, '1', 0)
buses[2].assign_route(routes, '1', 0)
print(buses[0].time_arr)
print(buses[0].event_arr)
print(buses[1].time_arr)
print(buses[1].event_arr)
print(buses[2].time_arr)
print(buses[2].event_arr)
next_bus_e(buses)

def available_bus(buses, dem_charge):
    print(buses)
    b_charges = [buses[i].charge for i in range(len(buses)) if buses[i].state==-1]
    b_index = [i for i in range(len(buses)) if buses[i].state==-1]
    index = np.nan
    if len(b_charges)>0:
        if (max(b_charges)>dem_charge):
            for i in range(len(b_charges)):
                if max(b_charges)==b_charges[i]:
                    index = b_index[i]
    return index

check = bus(20, 4)
buses = [bus(25, 5) for i in range(1)]
buses[0].state = 1
available_bus(buses, 20)

#### Testing for route demands

In [ ]:
# route demand functions
array_t = np.array(range(0, 12*60+1, 60))

a, b, c, d = 3, 2, 0, 75
plt.plot(array_t, np.ceil(a*np.sin((array_t+c)/d) + b), 
         color='r', label='bus_1', marker='o')

a, b, c, d = 2, 3, -180, 120
plt.plot(array_t, np.ceil(a*np.sin((array_t+c)/d) + b), 
         color='b', label='bus_2', marker='o')

a, b, c, d = 3, 3, 0, 45
plt.plot(array_t, np.ceil(a*np.sin((array_t+c)/d) + b), 
         color='g', label='bus_3', marker='o')

plt.xlabel('Time')
plt.ylabel('Buses')
plt.legend()
plt.show()